# Beyond Correlation: Why Likert-Scale Calibration Challenges LLM-as-Participant Designs.



# Code structure: #

In the **first block** of the code, some libraries (such as openai) are imported and the own API-key of OpenAI is defined.

In [ ]:
import os
from openai import OpenAI

os.environ["OPENAI_API_KEY"] = "" # insert here OpenAI API key


This is a test, it works! How can I assist you further?


The **second block** of the code contains the prompt engineering functions that we will use later. You will find zero and few shot prompting as example functions. However, only the zero-shot function is applied in the next steps, since few-shot prompting performed poorely in first pilot studies.

In [ ]:
import openai
from openai import OpenAI

# Function to perform zero-shot prompting
def zero_shot_prompting(task, prompt):
    """
    Performs zero-shot prompting by sending a prompt to the language model
    without providing any prior examples.

    Args:
    task (str): The task to be performed.
    prompt (str): The text input sent to the language model.

    Returns:
    str: The response from the language model.
    """
    # Create the chat message and send it to the language model
    response = client.chat.completions.create(
        model="o4-mini",
        messages=[
            {"role": "system", "content": "You are an assistant"},  # CHANGE HERE IF DESIRED
            {"role": "user", "content": prompt}  # User message with the actual prompt
        ]
    )
    # Return the content of the model’s first response message
    return response.choices[0].message.content


# Function to perform few-shot prompting
def few_shot_prompting(task, examples, prompt):
    """
    Performs few-shot prompting by providing some examples
    before sending the actual prompt to the language model.

    Args:
    task (str): The task to be performed.
    examples (list of dict): A list of examples, each example being a dictionary with 'input' and 'output'.
    prompt (str): The text input sent to the language model.

    Returns:
    str: The response from the language model.
    """
    # Initialize the messages list with a system message
    messages = [{"role": "system", "content": "You are an assistant"}]  # CHANGE HERE IF DESIRED

    # Add the examples to the messages
    for example in examples:
        messages.append({"role": "user", "content": example['input']})
        messages.append({"role": "assistant", "content": example['output']})

    # Add the actual prompt to the messages list
    messages.append({"role": "user", "content": prompt})

    # Create the chat message and send it to the language model
    response = client.chat.completions.create(
        model="o4-mini",
        messages=messages
    )
    # Return the content of the model’s first response message
    return response.choices[0].message.content


In the **third block** of the code you find code so that you can read in your uploaded data. This will be helpful in presenting the data to the LLM during prompting.

In [ ]:
import pandas as pd
import time
import json
import gc
from psutil import virtual_memory
from datetime import datetime
import random

# Load data
daten = 'Barbosa&Cat_2019.csv'  # Adjust the filename as needed
df = pd.read_csv(daten)

# Extract specific columns and pack them into a dictionary
columns_to_extract = ['French Sentences', 'syntactic position', 'trace position', 'status', 'gold_ratings']
selected_data = df[columns_to_extract].astype(str)
stimuli_dict = selected_data.to_dict(orient="index")

# Create list of items
all_items = [entry['French Sentences'] for entry in stimuli_dict.values()]
random.shuffle(all_items)
print("The materials for the study are:")
print(all_items)

The materials for the study are:
['a. Hector était propriétaire de plusieurs maisons, qu’il avait achetées à des époques différentes. Ses héritiers essayent d’identifier les propriétés à partir de photos. Ils se penchent sur la photo d’une belle maison art déco et demandent au notaire : b. Quand est-ce que c’est la maison qu’il a achetée ?', "a. Le cardinal s'indigne devant l'irrespect du portier. Il explose : b. Au pape, personne n’oserait lui parler ainsi.", 'a. Emilie voit un grand chien noir dans la rue. Étonnée, elle se tourne vers sa tante et s’exclame : b. C’est le chien que je l’ai vu chez toi.', 'a. Myriam a entendu un bruit suspect ce matin. Elle demande à son mari : b. Est-ce que tu sais qui, ce matin, est sorti par la porte de derrière ?', 'a. Natacha doit vider le grenier de sa grand-mère. Une amie lui demande : b. As-tu songé à qui, ces vieux objets, feraient plaisir ?', 'a. On a mis les petites filles en rang et on leur a posé des questions. L’un d’eux insiste : b. C’est

In the **fourth block** we can apply the prompt engineering functions of block 2. We will formulate our prompts in this cell. In this block, we can test different prompting strategies. We prompt the model as many times as we have (or want to have) particpants tu simulate.

In [ ]:
antworten_null_shot_all = {}
probanden_zahl= 60
reaction_time_per_participant=list()

import time  # Import the time module

for iteration in range(1, probanden_zahl + 1):  # Repeat the process
    print(f"### LLM-informant {iteration} ###")

    antworten_null_shot = {}  # Dictionary for null-shot responses in this iteration

    # === Null-Shot ===
    # Record the start time
    start_time_pro_part = time.time()

    for i, text in enumerate(all_items):
        start_time = time.time()
        zero_shot_prompt = f"Vous participez à une étude. Vous êtes de langue maternelle française. Tâche : Vous allez maintenant voir deux phrases. La phrase a constitue le contexte, la phrase b est la phrase que vous devez juger, pas la phrase a. Vous devez exprimer votre jugement seulement sur la phrase b en utilisant le schéma suivant : a. Je pourrais dire cela. b. Je pourrais dire cela, mais dans un autre contexte. c. Je ne pourrais pas dire cela, mais je connais des gens qui pourraient le faire. d. Personne ne dirait cela. e. Je ne sais pas. Vous donnez seulement la lettre, pas la justification. Penser : Vous lisez le contenu (phrase a), puis vous vous concentrez sur la phrase b. Vous la lisez attentivement et vous vous demandez si cette formulation est acceptable. Vous vous posez la question : Est-ce que moi, ou quelqu’un d’autre, pourrais dire cela ? Votre réponse vous aide à choisir la lettre qui exprimera votre jugement dans la tâche. Voici les deux phrases : '{text}' Réponse:"
        zero_shot = zero_shot_prompting("jugement d'acceptabilité", zero_shot_prompt)

        # Record the end time and calculate the elapsed time for this sentence
        elapsed_time = time.time() - start_time

        # Save the response in the dictionary with the index as the key
        antworten_null_shot[i] = {
            "Prompt": zero_shot_prompt,
            "Antwort": zero_shot,
            "Zeit": elapsed_time
        }

        #print(f"Input: {text}")
        print(f"Output: {zero_shot}")
        print(i,f"Time taken: {elapsed_time:.2f} seconds")
        print()

    # Calculate elapsed time for the iteration
    elapsed_time_pro_part = time.time() - start_time_pro_part

    # Save the null-shot results of this iteration in the parent dictionary
    antworten_null_shot_all[iteration] = antworten_null_shot
    reaction_time_per_participant.append(elapsed_time_pro_part)
    print(f"Elapsed time for iteration {iteration}: {elapsed_time_pro_part:.2f} seconds")
    print()

print(antworten_null_shot_all)
print("Mean reaction time per participant:", sum(reaction_time_per_participant)/len(reaction_time_per_participant))




Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.

Output: d
9 Time taken: 5.38 seconds

Output: a
10 Time taken: 5.17 seconds

Output: d
11 Time taken: 3.40 seconds

Output: d
12 Time taken: 2.63 seconds

Output: c
13 Time taken: 3.34 seconds

Output: d
14 Time taken: 6.91 seconds

Output: a
15 Time taken: 3.91 seconds

Output: c
16 Time taken: 3.83 seconds

Output: a
17 Time taken: 4.17 seconds

Output: d
18 Time taken: 3.60 seconds

Output: c
19 Time taken: 3.23 seconds

Output: c
20 Time taken: 4.14 seconds

Output: a
21 Time taken: 3.26 seconds

Output: d
22 Time taken: 3.62 seconds

Output: d
23 Time taken: 2.87 seconds

Output: a
24 Time taken: 2.36 seconds

Output: d
25 Time taken: 7.47 seconds

Output: d
26 Time taken: 2.66 seconds

Output: a
27 Time taken: 1.56 seconds

Output: a
28 Time taken: 3.72 seconds

Output: a
29 Time taken: 1.96 seconds

Output: a
30 Time taken: 2.17 seconds

Output: c
31 Time taken: 2.40 seconds

Output: d
32 Time taken: 4.37 second

In the **seventh block** we save the results from all test subjects in an Excel and csv file. These files subsequently store the answers of MULTIPLE test LLMs-participants.

In [ ]:
import pandas as pd
from datetime import datetime
columns_to_extract = ['French Sentences', 'syntactic position', 'trace position', 'status', 'gold_ratings']
# Dictionary to DataFrame conversion
def dict_to_dataframe(antworten_dict):
    rows = []
    for iteration, prompts in antworten_dict.items():
        for index, entry in prompts.items():
            for val in stimuli_dict.values():
                prompt_text = entry['Prompt']
                #print(val['French Sentences'])
                #print(prompt_text)
                #print(prompt_text.split("Voici les deux phrases :")[1])#.strip().replace("'", ""))
                prompt_cot=prompt_text.split("Voici les deux phrases :")[1].strip().replace("'", "")
                #print(prompt_cot.split("Réponse")[0].strip())
                if val['French Sentences'].strip() == prompt_cot.split("Réponse")[0].strip():
                  #print("yes")
                  rows.append({
                        "French Sentences": val['French Sentences'],
                        "syntactic position": val['syntactic position'],
                        "trace position": val['trace position'],
                        "status": val['status'],
                        "gold_ratings": val['gold_ratings'],
                        "Informant": iteration,
                        "Index": index,
                        "Prompt": entry["Prompt"],
                        "models_answer": entry["Antwort"],
                        "time": entry["Zeit"],
                        "date": datetime.now().strftime("%Y-%m-%d %H:%M:%S")
                    })
                else:
                  continue
                  #print("no",val['target_sent'].replace("'","").strip(),prompt_text.split("'non':")[1].split("Si")[0].strip().replace("'", ""))
    return pd.DataFrame(rows)

# Convert the dictionary to a DataFrame
new_data_df = dict_to_dataframe(antworten_null_shot_all)

# Save the DataFrame as new files
new_data_df.to_excel('all_accept_cotshot_gpt-4o-mini.xlsx', index=False)
new_data_df.to_csv('all_accept_cotshot_gpt-4o-mini.csv', index=False)

print("Data successfully saved!")


Die letzten 5000 Zeilen der Streamingausgabe wurden abgeschnitten.
 'a. Jules a reçu une enveloppe dans le courrier du matin. Il demande à son frère : b. Est-ce que le facteur a apporté ton paquet ?' Réponse:
a. Marie retrouve son amie Agnès pour la féliciter du succès de son mari. Elle lui dit : b. J’ai vu l’exposition que, ton mari, il organise.
Vous participez à une étude. Vous êtes de langue maternelle française. Tâche : Vous allez maintenant voir deux phrases. La phrase a constitue le contexte, la phrase b est la phrase que vous devez juger, pas la phrase a. Vous devez exprimer votre jugement seulement sur la phrase b en utilisant le schéma suivant : a. Je pourrais dire cela. b. Je pourrais dire cela, mais dans un autre contexte. c. Je ne pourrais pas dire cela, mais je connais des gens qui pourraient le faire. d. Personne ne dirait cela. e. Je ne sais pas. Vous donnez seulement la lettre, pas la justification. Penser : Vous lisez le contenu (phrase a), puis vous vous concentrez s